# Starting Point

In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

# Libraries

In [3]:
import pandas as pd
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_absolute_error
from sklearn.model_selection import train_test_split
from sklearn.impute import SimpleImputer
import seaborn as sns
import numpy as np
import os
import csv
import warnings

# Path and Df creation

In [7]:
train_path = '/Users/dyannarivera/Desktop/Newset/train_data.csv'
test_path = '/Users/dyannarivera/Desktop/Newset/test.csv'
submission_path = '/Users/dyannarivera/Desktop/Newset/newset-datathon-2022/SampleSubmission.csv'


In [8]:
train_set = pd.read_csv(train_path)
test_set = pd.read_csv(test_path)
sub_set = pd.read_csv(submission_path)

In [9]:
train_set.head(10)

ofd_date country_code                                  fc_codes  \
0  2021-06-30            C                          F6, F8, F14, F17   
1  2021-06-30            C                 F6, F8, F9, F14, F17, F18   
2  2021-06-30            C             F1, F4, F6, F7, F13, F15, F16   
3  2021-06-30            C  F2, F6, F7, F10, F12, F13, F14, F15, F19   
4  2021-06-30            C                     F6, F8, F13, F14, F17   
5  2021-06-30            C    F1, F2, F4, F6, F7, F13, F15, F16, F19   
6  2021-06-30            C                     F4, F8, F13, F14, F17   
7  2021-06-30            C                              F7, F12, F15   
8  2021-06-30            C                      F6, F7, F9, F10, F15   
9  2021-06-30            C                     F2, F8, F13, F14, F17   

  station_code    OFD   Slam  Earlies_Exp  Earlies_Rec  MNR_SNR_Exp  Rollover  \
0          D33  14594  14568          782          896          615       767   
1          D37  12736  13111          655          823          211        29   
2          D34  14562  15651         1028         1910          225        35   
3          D45  11165  11467          514          769           56        39   
4          D50  10006  10423          399          842           52        60   
5          D32  15707  16025          637          924           90       722   
6          D49   8640   8858          333          544           64        36   
7          D48  10695  11265          720         1246           70        42   
8          D42  10745  10892          867         1083          130       182   
9          D38  14355  14636          815         1120           77        58   

   Returns  R_Sideline  Sideline  
0       35           2         4  
1       17           2         1  
2       47           3         1  
3       29           0         1  
4       65           1         1  
5       52           2         3  
6       45           0         0  
7       36           1         1  
8       31           1         2  
9       88           3         2

# Data Exploration

In [10]:
train_set.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11309 entries, 0 to 11308
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   ofd_date      11309 non-null  object
 1   country_code  11309 non-null  object
 2   fc_codes      11309 non-null  object
 3   station_code  11309 non-null  object
 4   OFD           11309 non-null  int64 
 5   Slam          11309 non-null  int64 
 6   Earlies_Exp   11309 non-null  int64 
 7   Earlies_Rec   11309 non-null  int64 
 8   MNR_SNR_Exp   11309 non-null  int64 
 9   Rollover      11309 non-null  int64 
 10  Returns       11309 non-null  int64 
 11  R_Sideline    11309 non-null  int64 
 12  Sideline      11309 non-null  int64 
dtypes: int64(9), object(4)
memory usage: 1.1+ MB


In [11]:
train_set.shape

(11309, 13)

In [12]:
train_set.columns

Index(['ofd_date', 'country_code', 'fc_codes', 'station_code', 'OFD', 'Slam',
       'Earlies_Exp', 'Earlies_Rec', 'MNR_SNR_Exp', 'Rollover', 'Returns',
       'R_Sideline', 'Sideline'],
      dtype='object')

## Profile report (statistics)

In [13]:
from pandas_profiling import ProfileReport
report = ProfileReport(train_set)

report

# Data Cleaning

In [14]:
train_set.isnull().sum()
#no null values with test set neither

ofd_date        0
country_code    0
fc_codes        0
station_code    0
OFD             0
Slam            0
Earlies_Exp     0
Earlies_Rec     0
MNR_SNR_Exp     0
Rollover        0
Returns         0
R_Sideline      0
Sideline        0
dtype: int64

# Feature Engineering

## Country_code

In [15]:
#train_set.head(10)
train_set['country_code'].unique()

array(['C', 'A', 'B', 'D'], dtype=object)

In [16]:
train_set.head(10)

ofd_date country_code                                  fc_codes  \
0  2021-06-30            C                          F6, F8, F14, F17   
1  2021-06-30            C                 F6, F8, F9, F14, F17, F18   
2  2021-06-30            C             F1, F4, F6, F7, F13, F15, F16   
3  2021-06-30            C  F2, F6, F7, F10, F12, F13, F14, F15, F19   
4  2021-06-30            C                     F6, F8, F13, F14, F17   
5  2021-06-30            C    F1, F2, F4, F6, F7, F13, F15, F16, F19   
6  2021-06-30            C                     F4, F8, F13, F14, F17   
7  2021-06-30            C                              F7, F12, F15   
8  2021-06-30            C                      F6, F7, F9, F10, F15   
9  2021-06-30            C                     F2, F8, F13, F14, F17   

  station_code    OFD   Slam  Earlies_Exp  Earlies_Rec  MNR_SNR_Exp  Rollover  \
0          D33  14594  14568          782          896          615       767   
1          D37  12736  13111          655          823          211        29   
2          D34  14562  15651         1028         1910          225        35   
3          D45  11165  11467          514          769           56        39   
4          D50  10006  10423          399          842           52        60   
5          D32  15707  16025          637          924           90       722   
6          D49   8640   8858          333          544           64        36   
7          D48  10695  11265          720         1246           70        42   
8          D42  10745  10892          867         1083          130       182   
9          D38  14355  14636          815         1120           77        58   

   Returns  R_Sideline  Sideline  
0       35           2         4  
1       17           2         1  
2       47           3         1  
3       29           0         1  
4       65           1         1  
5       52           2         3  
6       45           0         0  
7       36           1         1  
8       31           1         2  
9       88           3         2

In [17]:
#Mapping (replacing) the letters by a number (encoding) it does not remove info
train_set['country_code'].replace(['A','B', 'C', 'D'],[0,1,2,3],inplace=True)
test_set['country_code'].replace(['A','B', 'C', 'D'],[0,1,2,3],inplace=True)

In [18]:
#Casting as integer following encoding (it was previously "object" which is not recommended)
train_set['country_code'] = train_set.country_code.astype('int64')
test_set['country_code'] = test_set.country_code.astype('int64')

## Fc_Codes

In [19]:
train_set['fc_codes'].nunique() 
#train_set['fc_codes'].unique()

60

## ofd_Date / station_code

In [20]:
#FEATURE ENGINEERING: ofd_date / station_code

#no actions since we need it untouched for creating "Id" columns

# Prediction Formatting (Id)

In [21]:
train_set['ofd_date'] = train_set.ofd_date.astype('string')
train_set['station_code'] = train_set.station_code.astype('string')

In [25]:
# CREATE PREDICTION FORMATING (Id)

#From Competition rules: Id: the combination of ofd_date (yyyy-mm-dd) and station (Dxx), joined by "_" (e.g. 2021-07-31_D33)

train_set["Id"] = train_set["ofd_date"] + "_" + train_set["station_code"]
test_set["Id"] = test_set["ofd_date"] + "_" + test_set["station_code"]

In [26]:
train_set['Id'] = train_set.Id.astype('string')
test_set['Id'] = test_set.Id.astype('string')

In [27]:
train_set.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11309 entries, 0 to 11308
Data columns (total 14 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   ofd_date      11309 non-null  string
 1   country_code  11309 non-null  int64 
 2   fc_codes      11309 non-null  object
 3   station_code  11309 non-null  string
 4   OFD           11309 non-null  int64 
 5   Slam          11309 non-null  int64 
 6   Earlies_Exp   11309 non-null  int64 
 7   Earlies_Rec   11309 non-null  int64 
 8   MNR_SNR_Exp   11309 non-null  int64 
 9   Rollover      11309 non-null  int64 
 10  Returns       11309 non-null  int64 
 11  R_Sideline    11309 non-null  int64 
 12  Sideline      11309 non-null  int64 
 13  Id            11309 non-null  string
dtypes: int64(10), object(1), string(3)
memory usage: 1.2+ MB


In [28]:
#Last column is "ID" respecting guidelines

train_set.head()

ofd_date  country_code                                  fc_codes  \
0  2021-06-30             2                          F6, F8, F14, F17   
1  2021-06-30             2                 F6, F8, F9, F14, F17, F18   
2  2021-06-30             2             F1, F4, F6, F7, F13, F15, F16   
3  2021-06-30             2  F2, F6, F7, F10, F12, F13, F14, F15, F19   
4  2021-06-30             2                     F6, F8, F13, F14, F17   

  station_code    OFD   Slam  Earlies_Exp  Earlies_Rec  MNR_SNR_Exp  Rollover  \
0          D33  14594  14568          782          896          615       767   
1          D37  12736  13111          655          823          211        29   
2          D34  14562  15651         1028         1910          225        35   
3          D45  11165  11467          514          769           56        39   
4          D50  10006  10423          399          842           52        60   

   Returns  R_Sideline  Sideline              Id  
0       35           2         4  2021-06-30_D33  
1       17           2         1  2021-06-30_D37  
2       47           3         1  2021-06-30_D34  
3       29           0         1  2021-06-30_D45  
4       65           1         1  2021-06-30_D50

# Define X and Y

In [29]:
test_set.head()

Unnamed: 0    ofd_date  country_code  \
0           0  2021-07-31             2   
1           1  2021-07-31             2   
2           2  2021-07-31             2   
3           3  2021-07-31             2   
4           4  2021-07-31             2   

                                   fc_codes station_code    OFD   Slam  \
0                          F6, F8, F14, F17          D33  10231  10957   
1                 F6, F8, F9, F14, F17, F18          D37  10113  10261   
2             F1, F4, F6, F7, F13, F15, F16          D34  11633  11789   
3  F2, F6, F7, F10, F12, F13, F14, F15, F19          D45   8633   8482   
4                     F6, F8, F13, F14, F17          D50   6972   7222   

   Earlies_Rec  Rollover  Returns  R_Sideline  Sideline              Id  
0          347        43       42           2       629  2021-07-31_D33  
1          285        50       25           0       165  2021-07-31_D37  
2          300        24       30           0       202  2021-07-31_D34  
3          180       713       24           1       276  2021-07-31_D45  
4          116        24       16           0       130  2021-07-31_D50

In [30]:
#Not using somes features which are interesting
features = ['OFD']
X = train_set[features]

# , 'Slam', 'Earlies_Rec', 'Rollover', 'Returns', 'R_Sideline', "Sideline",'Earlies_Exp','MNR_SNR_Exp']

#'fc_codes'
#'Earlies_Exp'
#'MNR_SNR_Exp'

In [31]:
# From Competition rules: [Target] = [Earlies_Exp] - [MNR_SNR_Exp]

y = train_set['Earlies_Exp'] - train_set['MNR_SNR_Exp']

# Prediction Formatting (Target)

In [32]:
train_set["# Expected"] = y

In [33]:
train_set.head()

ofd_date  country_code                                  fc_codes  \
0  2021-06-30             2                          F6, F8, F14, F17   
1  2021-06-30             2                 F6, F8, F9, F14, F17, F18   
2  2021-06-30             2             F1, F4, F6, F7, F13, F15, F16   
3  2021-06-30             2  F2, F6, F7, F10, F12, F13, F14, F15, F19   
4  2021-06-30             2                     F6, F8, F13, F14, F17   

  station_code    OFD   Slam  Earlies_Exp  Earlies_Rec  MNR_SNR_Exp  Rollover  \
0          D33  14594  14568          782          896          615       767   
1          D37  12736  13111          655          823          211        29   
2          D34  14562  15651         1028         1910          225        35   
3          D45  11165  11467          514          769           56        39   
4          D50  10006  10423          399          842           52        60   

   Returns  R_Sideline  Sideline              Id  # Expected  
0       35           2         4  2021-06-30_D33         167  
1       17           2         1  2021-06-30_D37         444  
2       47           3         1  2021-06-30_D34         803  
3       29           0         1  2021-06-30_D45         458  
4       65           1         1  2021-06-30_D50         347

In [34]:
train_set['SUM'] = train_set['Earlies_Exp'] - train_set['MNR_SNR_Exp']

In [35]:
train_set.head()

ofd_date  country_code                                  fc_codes  \
0  2021-06-30             2                          F6, F8, F14, F17   
1  2021-06-30             2                 F6, F8, F9, F14, F17, F18   
2  2021-06-30             2             F1, F4, F6, F7, F13, F15, F16   
3  2021-06-30             2  F2, F6, F7, F10, F12, F13, F14, F15, F19   
4  2021-06-30             2                     F6, F8, F13, F14, F17   

  station_code    OFD   Slam  Earlies_Exp  Earlies_Rec  MNR_SNR_Exp  Rollover  \
0          D33  14594  14568          782          896          615       767   
1          D37  12736  13111          655          823          211        29   
2          D34  14562  15651         1028         1910          225        35   
3          D45  11165  11467          514          769           56        39   
4          D50  10006  10423          399          842           52        60   

   Returns  R_Sideline  Sideline              Id  # Expected  SUM  
0       35           2         4  2021-06-30_D33         167  167  
1       17           2         1  2021-06-30_D37         444  444  
2       47           3         1  2021-06-30_D34         803  803  
3       29           0         1  2021-06-30_D45         458  458  
4       65           1         1  2021-06-30_D50         347  347

# Split 

In [36]:
train_X, val_X, train_y, val_y = train_test_split(X, y, random_state=1)

# Next Steps

In [39]:
#fit and predict the model (using Random Forest)
rf_model = RandomForestRegressor(random_state=500, warm_start=True)
rf_model.fit(train_X, train_y)
rf_val_predictions = rf_model.predict(val_X)
rf_val_mae = mean_absolute_error(rf_val_predictions, val_y)

In [40]:
#What is my MAE?
print("Validation MAE for Random Forest Model: {:,.0f}".format(rf_val_mae))

Validation MAE for Random Forest Model: 502


In [41]:
rf_model_for_test_data = RandomForestRegressor(random_state =500)

In [42]:
rf_model_for_test_data.fit(X,y)

RandomForestRegressor(random_state=500)

In [43]:
test_set['GRALL'] = test_set['OFD']- test_set['Slam'] + test_set['Earlies_Rec'] - test_set['Rollover'] - test_set['Returns'] - test_set['R_Sideline'] + test_set['Sideline']

In [44]:
test_set.head()

Unnamed: 0    ofd_date  country_code  \
0           0  2021-07-31             2   
1           1  2021-07-31             2   
2           2  2021-07-31             2   
3           3  2021-07-31             2   
4           4  2021-07-31             2   

                                   fc_codes station_code    OFD   Slam  \
0                          F6, F8, F14, F17          D33  10231  10957   
1                 F6, F8, F9, F14, F17, F18          D37  10113  10261   
2             F1, F4, F6, F7, F13, F15, F16          D34  11633  11789   
3  F2, F6, F7, F10, F12, F13, F14, F15, F19          D45   8633   8482   
4                     F6, F8, F13, F14, F17          D50   6972   7222   

   Earlies_Rec  Rollover  Returns  R_Sideline  Sideline              Id  GRALL  
0          347        43       42           2       629  2021-07-31_D33    163  
1          285        50       25           0       165  2021-07-31_D37    227  
2          300        24       30           0       202  2021-07-31_D34    292  
3          180       713       24           1       276  2021-07-31_D45   -131  
4          116        24       16           0       130  2021-07-31_D50    -44

In [45]:
features_test = ['GRALL']
# , 'Slam', 'Earlies_Rec', 'Rollover', 'Returns', 'R_Sideline', "Sideline"]

In [46]:
test_X = test_set[features_test]

In [47]:
test_preds = rf_model_for_test_data.predict(test_X)

In [48]:
sub_set.head()

Id  Expected
0  2021-07-31_D33       200
1  2021-07-31_D37       281
2  2021-07-31_D34       312
3  2021-07-31_D45        44
4  2021-07-31_D50       -20

In [50]:
sub_set

Id  Expected
0     2021-07-31_D33       200
1     2021-07-31_D37       281
2     2021-07-31_D34       312
3     2021-07-31_D45        44
4     2021-07-31_D50       -20
...              ...       ...
2384  2021-07-01_D60      -161
2385  2021-07-01_D54       140
2386  2021-07-01_D69       -86
2387  2021-07-01_D59       -44
2388  2021-07-01_D57       114

[2389 rows x 2 columns]

In [51]:
test_set.columns

Index(['Unnamed: 0', 'ofd_date', 'country_code', 'fc_codes', 'station_code',
       'OFD', 'Slam', 'Earlies_Rec', 'Rollover', 'Returns', 'R_Sideline',
       'Sideline', 'Id', 'GRALL'],
      dtype='object')

In [54]:
sub_set.head()

Id  Expected
0  2021-07-31_D33       200
1  2021-07-31_D37       281
2  2021-07-31_D34       312
3  2021-07-31_D45        44
4  2021-07-31_D50       -20

In [49]:
#How I save my work and make it into a CSV
output = pd.DataFrame({'Id': sub_set.Id, 
                       'Expected': test_preds})
output.to_csv('final_submission7.csv', index=False)
print('Your submission was successfully saved!')

Your submission was successfully saved!


In [50]:
# #Save ouput as a CSV file
# output = pd.DataFrame({'Id': test_data['Id'], 
#                        'Target': test_preds})
# output.to_csv('Datathon_2022.csv',index=False)
# print('Your submission was successfully saved!')